In [1]:
import sys
if ".." not in sys.path:
    sys.path.insert(0, "..")

In [2]:
import os
from datetime import date, timedelta
import pandas as pd
from information.terms_info import tags

pd.set_option('display.max_columns', None)
print(f'{tags}')

['flu', 'cough', 'fever', 'headache', 'lagnat', 'rashes', 'sipon', 'ubo', 'ecq', 'face-shield', 'Frontliners', 'masks', 'Quarantine', 'social-distancing', 'work-from-home']


In [3]:
"""
 Declare data scope
"""
# start_date = date.fromisoformat('2020-01-01')
start_date = date.fromisoformat('2020-03-16')
end_date   = date.fromisoformat('2021-02-15')

end_dates = []
current_date = start_date
while (current_date <= end_date):
    end_dates.append(str(current_date).replace('-', ' '))
    current_date += timedelta(days=1)
print(f"{len(end_dates)=}")

len(end_dates)=337


In [7]:
for tag in tags:
    normalize_tag = tag.replace('/', '.')
    #rsv_directory = os.path.abspath()
    msv_df_csv_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.csv')
    msv_df_pkl_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.pkl')

    msv_df = None

    for current_date in end_dates:
        current_rsv_path = os.path.join("C:\\Users\\Cheska Hung\\Desktop\\Thesis-GT Infodemiology\\-Thesis-Infodemiology-GT\\covid-19-google-trends-network\\scripts\\msvs\\data", normalize_tag, f"{current_date}.csv")
        rsv_df = pd.read_csv(current_rsv_path, parse_dates=['date'])
        rsv_df.drop(columns=['isPartial'], inplace=True)
        rsv_df.columns = ['date', 'index']

        if msv_df is None:
            msv_df = rsv_df.copy()
        else:
            # Join data into one
            merged_df = msv_df.merge(rsv_df, on='date', how='outer')

            # Calculate correction factors
            merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
            merged_df['correction_factor'] = merged_df['correction_factor'].fillna(1)
            merged_df['correction_factor'] = merged_df['correction_factor'].round(4)
            aggregated_correction_factor = merged_df['correction_factor'].mean()

            # Resclae the new RSV
            merged_df['index_y'] = merged_df['index_y'] * aggregated_correction_factor

            # Fill new data into previous RSV/MSV
            merged_df['index_x'] = merged_df['index_x'].fillna(merged_df['index_y'])
            print(merged_df.tail())
            
            msv_df = merged_df[['date', 'index_x']].copy()
            msv_df.columns = ['date', 'index']

        print(rsv_df.describe())
        
    msv_df.to_csv(msv_df_csv_path, index=False)
    msv_df.to_pickle(msv_df_pkl_path)

                      date       index
count                   31   31.000000
mean   2020-03-31 00:00:00   25.612903
min    2020-03-16 00:00:00   12.000000
25%    2020-03-23 12:00:00   15.500000
50%    2020-03-31 00:00:00   21.000000
75%    2020-04-07 12:00:00   31.000000
max    2020-04-15 00:00:00  100.000000
std                    NaN   16.819983
         date   index_x   index_y  correction_factor
27 2020-04-12  12.00000  48.74625             2.0833
28 2020-04-13  15.00000  58.49550             2.0000
29 2020-04-14  13.00000  50.69610             2.0000
30 2020-04-15  13.00000  52.64595             2.0769
31 2020-04-16  37.04715  37.04715             1.0000
                      date       index
count                   31   31.000000
mean   2020-04-01 00:00:00   45.645161
min    2020-03-17 00:00:00   19.000000
25%    2020-03-24 12:00:00   30.500000
50%    2020-04-01 00:00:00   41.000000
75%    2020-04-08 12:00:00   56.000000
max    2020-04-16 00:00:00  100.000000
std                

C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in div

         date    index_x    index_y  correction_factor
37 2020-04-22  99.228126  96.060114             0.9675
38 2020-04-23  57.911145  57.035693             0.9843
39 2020-04-24   0.000000   0.000000             1.0000
40 2020-04-25   0.000000   0.000000             1.0000
41 2020-04-26  65.040702  65.040702             1.0000
                      date       index
count                   31   31.000000
mean   2020-04-11 00:00:00   33.838710
min    2020-03-27 00:00:00    0.000000
25%    2020-04-03 12:00:00    0.000000
50%    2020-04-11 00:00:00    0.000000
75%    2020-04-18 12:00:00   67.000000
max    2020-04-26 00:00:00  100.000000
std                    NaN   39.068399
         date    index_x    index_y  correction_factor
38 2020-04-23  57.911145  56.636393             0.9843
39 2020-04-24   0.000000   0.000000             1.0000
40 2020-04-25   0.000000   0.000000             1.0000
41 2020-04-26  65.040702  64.585360             0.9994
42 2020-04-27   0.000000   0.000000         

C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: divide by zero encountered in di

         date  index_x  index_y  correction_factor
50 2020-05-05      0.0      NaN                1.0
51 2020-05-06      0.0      NaN                1.0
52 2020-05-07      0.0      NaN                1.0
53 2020-05-08      0.0      NaN                1.0
54 2020-05-09      NaN      NaN                1.0
                      date       index
count                   31   31.000000
mean   2020-04-24 00:00:00   21.225806
min    2020-04-09 00:00:00    0.000000
25%    2020-04-16 12:00:00    0.000000
50%    2020-04-24 00:00:00    0.000000
75%    2020-05-01 12:00:00   58.500000
max    2020-05-09 00:00:00  100.000000
std                    NaN   34.450650
         date  index_x  index_y  correction_factor
51 2020-05-06      0.0      0.0                1.0
52 2020-05-07      0.0      0.0                1.0
53 2020-05-08      0.0      0.0                1.0
54 2020-05-09      0.0      0.0                1.0
55 2020-05-10      0.0      0.0                1.0
                      date       inde

...

C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divid

          date    index_x    index_y  correction_factor
324 2021-02-03  46.659995  46.770100             1.0073
325 2021-02-04  74.501204  74.633138             1.0067
326 2021-02-05  41.746472  41.794557             1.0061
327 2021-02-06  45.749468  45.774991             1.0055
328 2021-02-07  64.682053  64.682053             1.0000
                      date       index
count                   31   31.000000
mean   2021-01-23 00:00:00   63.612903
min    2021-01-08 00:00:00    0.000000
25%    2021-01-15 12:00:00   50.500000
50%    2021-01-23 00:00:00   70.000000
75%    2021-01-30 12:00:00   77.000000
max    2021-02-07 00:00:00  100.000000
std                    NaN   22.880381
          date    index_x    index_y  correction_factor
325 2021-02-04  74.501204  74.677023             1.0067
326 2021-02-05  41.746472  41.819133             1.0061
327 2021-02-06  45.749468  45.801907             1.0055
328 2021-02-07  64.682053  64.720086             1.0049
329 2021-02-08  66.711474  66.711

C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divi

          date    index_x    index_y  correction_factor
338 2021-02-17  82.898760  83.026207             1.0012
339 2021-02-18  73.938297  74.023365             1.0008
340 2021-02-19  75.967884  76.023997             1.0004
341 2021-02-20   0.000000   0.000000             1.0000
342 2021-02-21  62.019576  62.019576             1.0000
                      date       index
count                   31   31.000000
mean   2021-02-06 00:00:00   59.741935
min    2021-01-22 00:00:00    0.000000
25%    2021-01-29 12:00:00   47.000000
50%    2021-02-06 00:00:00   65.000000
75%    2021-02-13 12:00:00   76.000000
max    2021-02-21 00:00:00  100.000000
std                    NaN   25.360031
          date    index_x    index_y  correction_factor
339 2021-02-18  73.938297  74.024738             1.0008
340 2021-02-19  75.967884  76.025407             1.0004
341 2021-02-20   0.000000   0.000000             1.0000
342 2021-02-21  62.019576  62.020727             0.9997
343 2021-02-22  58.019390  58.019

C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska Hung\AppData\Local\Temp\ipykernel_34340\3981812145.py:22: RuntimeWarning: invalid value encountered in divid